In [2]:
import csv

# Input and output file paths
input_file = 'measurements.csv'  # Replace with your input CSV file
output_file = 'dat_output.csv'  # Replace with your desired output file

# Read the CSV file
with open(input_file, mode='r', newline='', encoding='utf-8') as infile:
    reader = csv.DictReader(infile)
    # Sort the rows by 'measurement_id'
    sorted_rows = sorted(reader, key=lambda row: int(row['measurement_id']))

# Write the sorted rows to a new CSV file
with open(output_file, mode='w', newline='', encoding='utf-8') as outfile:
    writer = csv.DictWriter(outfile, fieldnames=reader.fieldnames)
    writer.writeheader()
    writer.writerows(sorted_rows)

print(f"File sorted by 'measurement_id' and saved to {output_file}")


File sorted by 'measurement_id' and saved to dat_output.csv


In [ ]:
import struct
import pandas as pd
import os

def read_binary_data(binary_file, start_offset, ele_offsets):
    """
    Reads and parses binary data from a file into a DataFrame.
    
     - Number of measurement (size of the dump) found in 0-7 (unsigned long long) 
     - local0 found in 8-11 (float)
     - local1 found in 12-15 (float)
     - var_local0 found in offset 16-19 (float)
     - var_local1 found in offset 20-23 (float)
     - geometry ID found in offset 24-31 (unsigned long long)
     - measurement_id found in offset 32-39 (unsigned long long)
     - cluster_link found in offset 40-47 (unsigned long long)
     - meas_dim found in offset 48-51 (unsigned int)

    Args:
        binary_file (str): Path to the binary file.
        start_offset (int): Offset to start reading from.
        ele_offsets (list): Byte offsets for unpacking.

    Returns:
        pd.DataFrame: DataFrame containing the parsed data.
    """
    # Define an empty DataFrame with the desired columns
    df = pd.DataFrame(columns=[
        "local0", "local1", "var_local0", "var_local1",
        "geometry_id", "measurement_id", "cluster_link", "meas_dim"
    ])

    # Get the total file size
    file_size = os.path.getsize(binary_file)

    # Read the binary data
    with open(binary_file, "rb") as bin_file:
        # mm = 
        print("number of measurements:", struct.unpack("Q", bin_file.read(8))[0])
        
        bin_file.seek(start_offset)
        raw_bytes = bin_file.read(file_size - start_offset)


    # Ensure offsets are consistent
    if len(ele_offsets) < 9:
        raise ValueError("ele_offsets must contain at least 9 elements for parsing.")

    # Process the binary data
    for i in range(0, len(raw_bytes), ele_offsets[-1]):
        try:
            new_data = {
                "local0": struct.unpack("f", raw_bytes[i + ele_offsets[0]: i + ele_offsets[1]])[0],
                "local1": struct.unpack("f", raw_bytes[i + ele_offsets[1]: i + ele_offsets[2]])[0],
                "var_local0": struct.unpack("f", raw_bytes[i + ele_offsets[2]: i + ele_offsets[3]])[0],
                "var_local1": struct.unpack("f", raw_bytes[i + ele_offsets[3]: i + ele_offsets[4]])[0],
                "geometry_id": struct.unpack("Q", raw_bytes[i + ele_offsets[4]: i + ele_offsets[5]])[0],
                "measurement_id": struct.unpack("Q", raw_bytes[i + ele_offsets[5]: i + ele_offsets[6]])[0],
                "cluster_link": struct.unpack("Q", raw_bytes[i + ele_offsets[6]: i + ele_offsets[7]])[0],
                "meas_dim": struct.unpack("I", raw_bytes[i + ele_offsets[7]: i + ele_offsets[8]])[0],
            }
            df = df.append(new_data, ignore_index=True)
        except struct.error:
            # Stop processing if there are not enough bytes left
            break

    return df

# Configuration
binary_file = "event000000001-measurements.dat"
start_offset = 8
ele_offsets = [0, 4, 8, 12, 16, 24, 32, 40, 44, 64]

# Read the binary data into a DataFrame
df = read_binary_data(binary_file, start_offset, ele_offsets)

# Save the DataFrame to a CSV file
csv_file = "measurements.csv"
df.to_csv(csv_file, index=False)

print(f"{binary_file} saved to {csv_file}")


number of measurements: 289890


C:\Users\laiji\AppData\Local\Temp\ipykernel_22464\389046238.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_data, ignore_index=True)
C:\Users\laiji\AppData\Local\Temp\ipykernel_22464\389046238.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_data, ignore_index=True)
C:\Users\laiji\AppData\Local\Temp\ipykernel_22464\389046238.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_data, ignore_index=True)
C:\Users\laiji\AppData\Local\Temp\ipykernel_22464\389046238.py:62: FutureWarning: The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.
  df = df.append(new_data, ignore_index=True)
C:\Users\laiji\A